This Jupyter notebook will use the SEAScope viewer and SEAScope Python bindings to retrieve inputs data 
* author: Lucile Gaultier, 
* date: 2022-11-30

To install SEAScope, follow the instructions on the [SEAScope website](https://seascope.oceandatalab.com/) and demonstrated in our ["SEAScope How To" YouTube playlist](https://www.youtube.com/playlist?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK).

To install the required Python packages, follow the instructions on https://pypi.org/project/SEAScope-env-OTC2023.
* **Windows** users can also follow the [Complete SEAScope install with Python modules for OTC23 on Windows](https://youtu.be/uomHRQPgqb8?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=3&t=132s) video on YouTube
* **macOS** users can also follow the [Installing SEAScope Python modules for OTC23 on macOS](https://youtu.be/w5f0ow6iPOY?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=6) video on YouTube

# Getting ready for St. Lehmkuhl data
Data from the Miam-New York St. Lehmkuhl cruise are studied. In-situ measurements from the ship are compared with SST and Chlorophyll remote sensing observations.


In this notebook, we will use different temperature products:
* The Temperature from the Ferrybox
* The GOES SST observation
* The S3 SLSTR SST observation

and biogeochemical parameters:
* The Total Concentration from the Ship
* The Chlorophyll-a from S3 OLCI

This notebook will teach you how to:
* Import data from a transect using SEAScope
* Compare in-situ transects with satellite images

<div class="alert alert-warning">

**This notebook uses the following data collection:**

* directory: `echosounder`, label: `Echosounder`
* directory: `Blueferrybox`, label: `Blueferrybox`
* directory: `cmems_blueferrybox`, label: `CMEMS Blueferrybox QC`
* directory: `sentinel3_slstr_l1_bt`, label: `sentinel3 slstr l1 bt`
* directory: `goes16`, label: `GOES16 SST`
* directory: `sentinel3_olci_l2_wfr`, label `sentinel3 olci l2 wfr`
Check that you have them in your SEAScope catalogue before continuing with this notebook.\
If not, you can download an archive containing them at https://ftp.odl.bzh/odl/events/otc23/data_ila14.zip.

To learn how to add data to SEAScope, you can watch one of the following YouTube videos:
* [How to add data to SEAScope on **Windows**](https://youtu.be/TsJSg7V7WNU?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=2)
    * or the "Add data to SEAScope" chapter of [How to add data to SEAScope on **Windows**](https://youtu.be/uomHRQPgqb8?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=3&t=40s)
* [How to add data to SEAScope on **macOS**](https://youtu.be/s5X3ewpmcuw?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=5)
* [How to add data to SEAScope on **Linux**](https://youtu.be/3ZAzgl3v2lo?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=8)

</div>

In [ ]:
# Import necessary modules
%matplotlib inline
import matplotlib.pyplot as plt
import numpy
import contextlib
import os
import datetime


## 1. Find the data of interest in SEAScope

##### Select and locate the data in the SEAScope viewer

1. In the "Catalogue" (the panel on the right), select one or more of the following:
    * collection `Blueferrybox`, variable `BlueInsight_FerryBox.INLET_Temperature`
    * collection `CMEMS Blueferrybox QC`, variable `Temperature`

    * collection `sentinel3 slstr l1 bt`, variable `sea_surface_temperature`
    * collection `GOES16 SST`, variable `sea_surface_temperature`
2. Go to the date where have the different data available and a small cloud cover over the Gulf Stream and select a three days time span
    * The 14<sup>th</sup> of December 2021
3. Zoom into the Gulf Stream region

## 2. Get data from the SEAScope viewer using the python bindings

##### Extract the data from SEAScope

1. Click on the transect from Blueferrybox collection, a "Selected granule" panel should open
2. Extract the data intersecting that transect by clicking on the extract button in the "Selected granule" panel


Load the extracted data

In [ ]:
# Load data directly from viewer memory
from SEAScope.lib import get_extracted_data
extractions = get_extracted_data()

Identify current granules among the extracted data

In [ ]:
tra_granules = []

for k, (granule_path, granule_info) in enumerate(extractions.items()):
    granule_name = os.path.basename(granule_path)
    print(granule_name)
    # Print extracted granule data 
    print(f'{k} - {granule_name}')
    print('\n'.join([f'\t{_}' for _ in granule_info['data']]))

    if 'GOES' in granule_name:
        name_tra = 'GOES'
        tra = granule_info['data']['sea_surface_temperature']
        label = 'temperature'
    elif 'traj' in granule_name:
        for key in granule_info['data'].keys():
            if 'Temperature' in key:
                name_tra = key
                tra = granule_info['data'][key]
                label = 'temperature'
            elif 'TEMP' in key:
                name_tra = 'CMEMS ferrybox'
                tra = granule_info['data']['TEMP']
                label = 'temperature'
            elif 'Total_Conc' in key:
                name_tra = 'Echosounder total conc'
                tra = numpy.log(granule_info['data']['Total_Conc'])
                label = 'concentration'
            elif 'Temp_Sensor' in key:
                name_tra = 'Echosounder temperature'
                tra = numpy.log(granule_info['data']['Temp_Sensor'])
                label = 'temperature'
            else:
                continue
            tra_granules.append({'granule_info': granule_info,
                                 'name': name_tra,
                                 'tra': tra,
                                 'label': label,
                                 })
    elif 'S3A_SL' in granule_name or 'S3B_SL' in granule_name:
        label = 'temperature'
        name_tra = 'S3 SLSTR'
        tra = granule_info['data']['sea_surface_temperature']    
    elif 'S3A_OL' in granule_name or 'S3B_OL' in granule_name:
        label = 'concentration'
        name_tra = 'S3 OLCI'
        tra = granule_info['data']['CHL_OC4ME']    
    else:
        continue
    if 'traj' not in granule_name:
        tra_granules.append({
            'granule_info': granule_info,
            'name': name_tra,
            'tra': tra,
            'label': label,
        })

if len(tra_granules) == 0:
    print('Wrong collections selected, go back to SEAScope and select at least one of the following:')
   
    raise Exception('See issues above')

# Make sure the result is reset
granule_id = None

## 3. Plot the extracted data

In [ ]:
# Plot all the extracted data as a function of the latitude
fig, ax =  plt.subplots(figsize=(16, 10))
list_labels = [tra_granule['label'] for tra_granule in tra_granules]
ax2 = ax.twinx()
for tra_granule in tra_granules:
    # Get latitude coordinate
    lat = [_dic['lat'] for _dic in tra_granule['granule_info']['meta']['gcps']]
    # Get variables
    _var = tra_granule['tra'].copy()
    _var = numpy.ma.array(_var.flatten(), mask=_var.mask)
    _label = tra_granule['label']
    if _label == 'concentration':
        print(tra_granule['name'])
        _var = (_var - numpy.mean(_var)) / numpy.std(_var)
        ax2.plot(lat, _var, '--', label=tra_granule['name'])
    else:
        ax.plot(lat, _var, label=tra_granule['name'])
ax.set_xlabel('Latitudes')
if 'temperature' in list_labels:
    ax.set_ylabel('temperature')
    ax.legend(loc='upper left', title='temperature')
if 'concentration' in list_labels:
    ax2.set_ylabel('concentration')
    ax2.legend(loc='upper right', title='cencentration')



Plot the velocity norm, vectorfield and the flow computed on frontal structure

## 4. Run the Jupyter from the section looking at the biogeochemistry instead of sst

##### Select and locate the data in the SEAScope viewer

1. In the "Catalogue" (the panel on the right), select one or more of the following:
    * collection `Echosounder`, variable `Total Conc`
    * collection `sentinel3 olci l2 wfr`, variable `CHL_OC4ME`
2. Go to the date where have the different data available and a small cloud cover over the Gulf Stream, select a three days time span
    * The 14<sup>th</sup> of December 2021
3. Zoom into the Gulf Stream region

4. Go back to section 2 to get data from SEAScope and run the Jupyter